## Technical Indicators List

All the indicators that https://pypi.org/project/stockstats/ supports

In [1]:
INDICATORS_LIST_ALL = ['high_5_sma','rsi','boll','macd','cr','wr','cci','tr','atr','dma','pdi','dx','adx','adxr','trix','tema','vr','mfi','vwma',
                   'chop','ppo','stochrsi','supertrend','aroon','close_75_z','ao'
                   ]

In [2]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import matplotlib.dates as mdates
#%matplotlib inline
import mplfinance as mpf # matplot.finance to plot candlesticks
import random
import itertools # iterators for efficient looping: https://docs.python.org/3/library/itertools.html 

from finrl.meta.preprocessor.yahoodownloader import YahooDownloader # a veces puede dar error al hacer fetch de la data porque no encuentra un stock o sus precios, o por la timezone
from finrl import config_tickers # config_tickers es una clase en la que se guardan en listas los nombres de cada stock para cada índice
from finrl.meta.preprocessor.preprocessors import FeatureEngineer, data_split
from finrl.meta.env_stock_trading.env_stocktrading import StockTradingEnv
from finrl.agents.stablebaselines3.models import DRLAgent
from stable_baselines3.common.logger import configure
from finrl.plot import backtest_stats, backtest_plot, get_daily_return, get_baseline

/Users/carolinaalbamaruganrubio/miniforge3/envs/ai4finance/lib/python3.10/site-packages/pyfolio/pos.py:26: UserWarning: Module "zipline.assets" not found; mutltipliers will not be applied to position notionals.
  warnings.warn(


In [3]:
TRAIN_START_DATE = '2010-01-01'
TRAIN_END_DATE = '2021-10-01'
TEST_START_DATE = '2021-10-01'
TEST_END_DATE = '2023-03-01'

In [4]:
stock = YahooDownloader(start_date = TRAIN_START_DATE,
                     end_date = TEST_END_DATE,
                     ticker_list = config_tickers.DOW_30_TICKER).fetch_data()

[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%*******

Shape of DataFrame:  (97013, 8)


In [5]:
stock # this DF contains all the stock price history from the train start date to the test end date, for every firm in the DJ30

date        open        high         low       close     volume  \
0      2010-01-04    7.622500    7.660714    7.585000    6.470740  493729600   
1      2010-01-04   56.630001   57.869999   56.560001   41.200798    5277400   
2      2010-01-04   40.810001   41.099998   40.389999   33.090435    6894300   
3      2010-01-04   55.720001   56.389999   54.799999   43.777542    6186700   
4      2010-01-04   57.650002   59.189999   57.509998   40.190224    7325600   
...           ...         ...         ...         ...         ...        ...   
97008  2023-02-28  482.670013  483.359985  473.920013  465.066833    3902100   
97009  2023-02-28  220.000000  221.770004  219.500000  217.824539    5385400   
97010  2023-02-28   38.700001   38.970001   38.549999   35.538387   16685300   
97011  2023-02-28   35.480000   35.779999   35.320000   32.750977    8847000   
97012  2023-02-28   47.000000   47.549999   46.983334   46.346088   18054000   

        tic  day  
0      AAPL    0  
1      AMGN    0  
2       AXP    0  
3        BA    0  
4       CAT    0  
...     ...  ...  
97008   UNH    1  
97009     V    1  
97010    VZ    1  
97011   WBA    1  
97012   WMT    1  

[97013 rows x 8 columns]

In [6]:
stock.day.describe()

count    97013.000000
mean         2.024131
std          1.398530
min          0.000000
25%          1.000000
50%          2.000000
75%          3.000000
max          4.000000
Name: day, dtype: float64

Stock symbols

In [7]:
tickers = stock.tic.unique()

We wanted to get:

In [8]:
print(np.reshape(config_tickers.DOW_30_TICKER, (len(config_tickers.DOW_30_TICKER))))
print("Number of firms in the index: ",len(config_tickers.DOW_30_TICKER))

['AXP' 'AMGN' 'AAPL' 'BA' 'CAT' 'CSCO' 'CVX' 'GS' 'HD' 'HON' 'IBM' 'INTC'
 'JNJ' 'KO' 'JPM' 'MCD' 'MMM' 'MRK' 'MSFT' 'NKE' 'PG' 'TRV' 'UNH' 'CRM'
 'VZ' 'V' 'WBA' 'WMT' 'DIS' 'DOW']
Number of firms in the index:  30


Creo que DOW es el DJIA, la media

But we got (because of the unavailable timezone or price data):

In [9]:
print(tickers) # stocks we have to train the agent
print("Number of firms downloaded: ",len(tickers))

['AAPL' 'AMGN' 'AXP' 'BA' 'CAT' 'CRM' 'CSCO' 'CVX' 'DIS' 'GS' 'HD' 'HON'
 'IBM' 'INTC' 'JNJ' 'JPM' 'KO' 'MCD' 'MMM' 'MRK' 'MSFT' 'NKE' 'PG' 'TRV'
 'UNH' 'V' 'VZ' 'WBA' 'WMT' 'DOW']
Number of firms downloaded:  30


## Agent 1+

with following technical indicators:

In [10]:
# let's first take 4 technical indicators randomly from the supported indicators list
INDICATORS = ['high_5_sma','boll','stochrsi','adx','close_75_z','ao']

In [11]:
INDICATORS

['high_5_sma', 'boll', 'stochrsi', 'adx', 'close_75_z', 'ao']

In [12]:
# creamos instancia de FeatureEngineer indicando la configuración deseada para hacer el preproceso
fe = FeatureEngineer(
                    use_technical_indicator=True,
                    tech_indicator_list = INDICATORS,
                    use_vix=True, # AUN NO SE QUE ES ESTO
                    use_turbulence=True, # measures extreme asset price fluctuation --> if the turbulence index reaches a pre-defined threshold, the agent will halt buying action and start selling the holding shares gradually
                    user_defined_feature = False) # MIRA A VER QUÉ ERA DEFINIRSE UNA FEATURE (creo que es )

processed = fe.preprocess_data(stock)

[*********************100%%**********************]  1 of 1 completed

Successfully added technical indicators
Shape of DataFrame:  (3310, 8)


Successfully added vix
Successfully added turbulence index


Comentario: hay indicadores que pese a estar documentados como soportados en https://pypi.org/project/stockstats/, esta versión de código no los reconoce. Habrá que comprobar mediante más pruebas que todos los incluídos en la lista de todos los indicadores, estén soportados por esta versión. 

In [13]:
processed

date        open        high         low       close     volume  \
0      2010-01-04    7.622500    7.660714    7.585000    6.470740  493729600   
1      2010-01-04   56.630001   57.869999   56.560001   41.200798    5277400   
2      2010-01-04   40.810001   41.099998   40.389999   33.090435    6894300   
3      2010-01-04   55.720001   56.389999   54.799999   43.777542    6186700   
4      2010-01-04   57.650002   59.189999   57.509998   40.190224    7325600   
...           ...         ...         ...         ...         ...        ...   
95985  2023-02-27  488.769989  490.940002  481.959991  472.278198    3006200   
95986  2023-02-27  220.729996  221.440002  219.339996  218.230591    4255300   
95987  2023-02-27   38.990002   39.150002   38.630001   35.602486   14210900   
95988  2023-02-27   36.049999   36.080002   35.270000   32.621925    5580100   
95989  2023-02-27   47.570000   47.696667   46.886665   46.121086   16647300   

        tic  day  high_5_sma        boll   stochrsi         adx  close_75_z  \
0      AAPL    0    7.660714    6.470740   0.000000  100.000000    0.000000   
1      AMGN    0   57.869999   41.200798   0.000000  100.000000    0.000000   
2       AXP    0   41.099998   33.090435   0.000000  100.000000    0.000000   
3        BA    0   56.389999   43.777542   0.000000  100.000000    0.000000   
4       CAT    0   59.189999   40.190224   0.000000  100.000000    0.000000   
...     ...  ...         ...         ...        ...         ...         ...   
95985   UNH    0  494.414001  476.145312  32.661437   11.867177   -1.131985   
95986     V    0  221.592001  224.423517   7.819466   41.614291    0.455638   
95987    VZ    0   39.360000   36.881721  26.473435   40.124667   -0.081318   
95988   WBA    0   36.282000   33.398429   2.329875   26.347004   -1.184411   
95989   WMT    0   48.407333   46.782871  15.558425   24.757027   -0.969926   

             ao        vix  turbulence  
0      0.000000  20.040001    0.000000  
1      0.000000  20.040001    0.000000  
2      0.000000  20.040001    0.000000  
3      0.000000  20.040001    0.000000  
4      0.000000  20.040001    0.000000  
...         ...        ...         ...  
95985  1.691383  20.950001    7.163887  
95986 -4.844647  20.950001    7.163887  
95987 -1.411559  20.950001    7.163887  
95988 -0.406441  20.950001    7.163887  
95989 -0.022863  20.950001    7.163887  

[95990 rows x 16 columns]

In order to allow the Agent to have a consistent data structure to work with, we need to ensure that each stock has the same data range. This is necessary because not all stocks have data for every trading day due to holidays, stock-specific trading suspensions, or newly listed stocks. Therefore, we will establish a common data interval for each stock with day granularity and fill with 0 the (the more NaNs we have, the worst the performance will be). --> We can check this effect with other Stock Indices with less missing stock prices.

Convert the stock column to list

In [14]:
list_ticker = processed["tic"].unique().tolist()
print(list_ticker)
len(list_ticker)

['AAPL', 'AMGN', 'AXP', 'BA', 'CAT', 'CRM', 'CSCO', 'CVX', 'DIS', 'GS', 'HD', 'HON', 'IBM', 'INTC', 'JNJ', 'JPM', 'KO', 'MCD', 'MMM', 'MRK', 'MSFT', 'NKE', 'PG', 'TRV', 'UNH', 'V', 'VZ', 'WBA', 'WMT']


29

Create a list from the minimum to the maximum date and with the same granularity

In [15]:
list_date = list(pd.date_range(processed['date'].min(),processed['date'].max()).astype(str))
list_date

['2010-01-04',
 '2010-01-05',
 '2010-01-06',
 '2010-01-07',
 '2010-01-08',
 '2010-01-09',
 '2010-01-10',
 '2010-01-11',
 '2010-01-12',
 '2010-01-13',
 '2010-01-14',
 '2010-01-15',
 '2010-01-16',
 '2010-01-17',
 '2010-01-18',
 '2010-01-19',
 '2010-01-20',
 '2010-01-21',
 '2010-01-22',
 '2010-01-23',
 '2010-01-24',
 '2010-01-25',
 '2010-01-26',
 '2010-01-27',
 '2010-01-28',
 '2010-01-29',
 '2010-01-30',
 '2010-01-31',
 '2010-02-01',
 '2010-02-02',
 '2010-02-03',
 '2010-02-04',
 '2010-02-05',
 '2010-02-06',
 '2010-02-07',
 '2010-02-08',
 '2010-02-09',
 '2010-02-10',
 '2010-02-11',
 '2010-02-12',
 '2010-02-13',
 '2010-02-14',
 '2010-02-15',
 '2010-02-16',
 '2010-02-17',
 '2010-02-18',
 '2010-02-19',
 '2010-02-20',
 '2010-02-21',
 '2010-02-22',
 '2010-02-23',
 '2010-02-24',
 '2010-02-25',
 '2010-02-26',
 '2010-02-27',
 '2010-02-28',
 '2010-03-01',
 '2010-03-02',
 '2010-03-03',
 '2010-03-04',
 '2010-03-05',
 '2010-03-06',
 '2010-03-07',
 '2010-03-08',
 '2010-03-09',
 '2010-03-10',
 '2010-03-

Assign every day to each stock

In [16]:
combination = list(itertools.product(list_date,list_ticker))
combination

[('2010-01-04', 'AAPL'),
 ('2010-01-04', 'AMGN'),
 ('2010-01-04', 'AXP'),
 ('2010-01-04', 'BA'),
 ('2010-01-04', 'CAT'),
 ('2010-01-04', 'CRM'),
 ('2010-01-04', 'CSCO'),
 ('2010-01-04', 'CVX'),
 ('2010-01-04', 'DIS'),
 ('2010-01-04', 'GS'),
 ('2010-01-04', 'HD'),
 ('2010-01-04', 'HON'),
 ('2010-01-04', 'IBM'),
 ('2010-01-04', 'INTC'),
 ('2010-01-04', 'JNJ'),
 ('2010-01-04', 'JPM'),
 ('2010-01-04', 'KO'),
 ('2010-01-04', 'MCD'),
 ('2010-01-04', 'MMM'),
 ('2010-01-04', 'MRK'),
 ('2010-01-04', 'MSFT'),
 ('2010-01-04', 'NKE'),
 ('2010-01-04', 'PG'),
 ('2010-01-04', 'TRV'),
 ('2010-01-04', 'UNH'),
 ('2010-01-04', 'V'),
 ('2010-01-04', 'VZ'),
 ('2010-01-04', 'WBA'),
 ('2010-01-04', 'WMT'),
 ('2010-01-05', 'AAPL'),
 ('2010-01-05', 'AMGN'),
 ('2010-01-05', 'AXP'),
 ('2010-01-05', 'BA'),
 ('2010-01-05', 'CAT'),
 ('2010-01-05', 'CRM'),
 ('2010-01-05', 'CSCO'),
 ('2010-01-05', 'CVX'),
 ('2010-01-05', 'DIS'),
 ('2010-01-05', 'GS'),
 ('2010-01-05', 'HD'),
 ('2010-01-05', 'HON'),
 ('2010-01-05', 'IB

Merge with stock DF (potentially resulting in NaN values)

In [17]:
processed_full = pd.DataFrame(combination,columns=["date","tic"]).merge(processed,on=["date","tic"],how="left")

Remove non-trading days generated with the date range

In [18]:
processed_full = processed_full[processed_full['date'].isin(processed['date'])]

In [19]:
processed_full

date   tic        open        high         low       close  \
0       2010-01-04  AAPL    7.622500    7.660714    7.585000    6.470740   
1       2010-01-04  AMGN   56.630001   57.869999   56.560001   41.200798   
2       2010-01-04   AXP   40.810001   41.099998   40.389999   33.090435   
3       2010-01-04    BA   55.720001   56.389999   54.799999   43.777542   
4       2010-01-04   CAT   57.650002   59.189999   57.509998   40.190224   
...            ...   ...         ...         ...         ...         ...   
139282  2023-02-27   UNH  488.769989  490.940002  481.959991  472.278198   
139283  2023-02-27     V  220.729996  221.440002  219.339996  218.230591   
139284  2023-02-27    VZ   38.990002   39.150002   38.630001   35.602486   
139285  2023-02-27   WBA   36.049999   36.080002   35.270000   32.621925   
139286  2023-02-27   WMT   47.570000   47.696667   46.886665   46.121086   

             volume  day  high_5_sma        boll   stochrsi         adx  \
0       493729600.0  0.0    7.660714    6.470740   0.000000  100.000000   
1         5277400.0  0.0   57.869999   41.200798   0.000000  100.000000   
2         6894300.0  0.0   41.099998   33.090435   0.000000  100.000000   
3         6186700.0  0.0   56.389999   43.777542   0.000000  100.000000   
4         7325600.0  0.0   59.189999   40.190224   0.000000  100.000000   
...             ...  ...         ...         ...        ...         ...   
139282    3006200.0  0.0  494.414001  476.145312  32.661437   11.867177   
139283    4255300.0  0.0  221.592001  224.423517   7.819466   41.614291   
139284   14210900.0  0.0   39.360000   36.881721  26.473435   40.124667   
139285    5580100.0  0.0   36.282000   33.398429   2.329875   26.347004   
139286   16647300.0  0.0   48.407333   46.782871  15.558425   24.757027   

        close_75_z        ao        vix  turbulence  
0         0.000000  0.000000  20.040001    0.000000  
1         0.000000  0.000000  20.040001    0.000000  
2         0.000000  0.000000  20.040001    0.000000  
3         0.000000  0.000000  20.040001    0.000000  
4         0.000000  0.000000  20.040001    0.000000  
...            ...       ...        ...         ...  
139282   -1.131985  1.691383  20.950001    7.163887  
139283    0.455638 -4.844647  20.950001    7.163887  
139284   -0.081318 -1.411559  20.950001    7.163887  
139285   -1.184411 -0.406441  20.950001    7.163887  
139286   -0.969926 -0.022863  20.950001    7.163887  

[95990 rows x 16 columns]

In [20]:
len(processed_full.tic.unique())

29

In [21]:
processed_full.info()

<class 'pandas.core.frame.DataFrame'>
Index: 95990 entries, 0 to 139286
Data columns (total 16 columns):
 #   Column      Non-Null Count  Dtype  
---  ------      --------------  -----  
 0   date        95990 non-null  object 
 1   tic         95990 non-null  object 
 2   open        95990 non-null  float64
 3   high        95990 non-null  float64
 4   low         95990 non-null  float64
 5   close       95990 non-null  float64
 6   volume      95990 non-null  float64
 7   day         95990 non-null  float64
 8   high_5_sma  95990 non-null  float64
 9   boll        95990 non-null  float64
 10  stochrsi    95990 non-null  float64
 11  adx         95990 non-null  float64
 12  close_75_z  95990 non-null  float64
 13  ao          95990 non-null  float64
 14  vix         95990 non-null  float64
 15  turbulence  95990 non-null  float64
dtypes: float64(14), object(2)
memory usage: 12.4+ MB


In [22]:
processed_full.describe()

open          high           low         close        volume  \
count  95990.000000  95990.000000  95990.000000  95990.000000  9.599000e+04   
mean     102.224117    103.175365    101.253646     88.243726  1.995383e+07   
std       73.520545     74.279832     72.738958     70.607970  6.204278e+07   
min        6.870357      7.000000      6.794643      5.806765  3.054000e+05   
25%       47.470001     47.910000     47.020000     38.935163  4.003909e+06   
50%       83.498051     84.139999     82.830002     67.654839  7.250700e+06   
75%      138.477531    139.731735    137.169998    118.501167  1.498672e+07   
max      555.000000    558.099976    550.130005    540.800171  1.880998e+09   

                day    high_5_sma          boll      stochrsi           adx  \
count  95990.000000  95990.000000  95990.000000  95990.000000  95990.000000   
mean       2.024471    103.102538     87.865634     52.333616     32.298525   
std        1.398649     74.216049     70.270855     36.170209     16.015211   
min        0.000000      7.045357      5.992488      0.000000      3.794128   
25%        1.000000     47.854000     38.850000     18.107336     19.771846   
50%        2.000000     84.121000     67.250128     53.860009     29.001860   
75%        3.000000    139.601499    118.195925     87.766690     42.248642   
max        4.000000    553.847998    524.565884    100.000000    100.000000   

         close_75_z            ao           vix    turbulence  
count  95990.000000  95990.000000  95990.000000  95990.000000  
mean       0.417570      0.542043     18.721163     34.943606  
std        1.337794      5.719594      7.269653     43.065944  
min       -5.414782   -159.193413      9.140000      0.000000  
25%       -0.571311     -1.110588     13.630000     14.972940  
50%        0.635934      0.488779     16.875000     24.175838  
75%        1.457174      2.307581     21.760000     40.000708  
max        5.784537     62.724292     82.690002    652.614185

In this case, there are no nulls, but if there were we would need to fill them in the following way. 

In [23]:
processed_full = processed_full.sort_values(['date','tic']) # we need to sort bc of the data_split method CHECK SOURCE CODE 

processed_full = processed_full.fillna(0)

In [24]:
processed_full.describe()

open          high           low         close        volume  \
count  95990.000000  95990.000000  95990.000000  95990.000000  9.599000e+04   
mean     102.224117    103.175365    101.253646     88.243726  1.995383e+07   
std       73.520545     74.279832     72.738958     70.607970  6.204278e+07   
min        6.870357      7.000000      6.794643      5.806765  3.054000e+05   
25%       47.470001     47.910000     47.020000     38.935163  4.003909e+06   
50%       83.498051     84.139999     82.830002     67.654839  7.250700e+06   
75%      138.477531    139.731735    137.169998    118.501167  1.498672e+07   
max      555.000000    558.099976    550.130005    540.800171  1.880998e+09   

                day    high_5_sma          boll      stochrsi           adx  \
count  95990.000000  95990.000000  95990.000000  95990.000000  95990.000000   
mean       2.024471    103.102538     87.865634     52.333616     32.298525   
std        1.398649     74.216049     70.270855     36.170209     16.015211   
min        0.000000      7.045357      5.992488      0.000000      3.794128   
25%        1.000000     47.854000     38.850000     18.107336     19.771846   
50%        2.000000     84.121000     67.250128     53.860009     29.001860   
75%        3.000000    139.601499    118.195925     87.766690     42.248642   
max        4.000000    553.847998    524.565884    100.000000    100.000000   

         close_75_z            ao           vix    turbulence  
count  95990.000000  95990.000000  95990.000000  95990.000000  
mean       0.417570      0.542043     18.721163     34.943606  
std        1.337794      5.719594      7.269653     43.065944  
min       -5.414782   -159.193413      9.140000      0.000000  
25%       -0.571311     -1.110588     13.630000     14.972940  
50%        0.635934      0.488779     16.875000     24.175838  
75%        1.457174      2.307581     21.760000     40.000708  
max        5.784537     62.724292     82.690002    652.614185

In [25]:
large_value = 1e9

processed_full.replace([np.inf], large_value, inplace=True)

In [26]:
processed_full.describe()

open          high           low         close        volume  \
count  95990.000000  95990.000000  95990.000000  95990.000000  9.599000e+04   
mean     102.224117    103.175365    101.253646     88.243726  1.995383e+07   
std       73.520545     74.279832     72.738958     70.607970  6.204278e+07   
min        6.870357      7.000000      6.794643      5.806765  3.054000e+05   
25%       47.470001     47.910000     47.020000     38.935163  4.003909e+06   
50%       83.498051     84.139999     82.830002     67.654839  7.250700e+06   
75%      138.477531    139.731735    137.169998    118.501167  1.498672e+07   
max      555.000000    558.099976    550.130005    540.800171  1.880998e+09   

                day    high_5_sma          boll      stochrsi           adx  \
count  95990.000000  95990.000000  95990.000000  95990.000000  95990.000000   
mean       2.024471    103.102538     87.865634     52.333616     32.298525   
std        1.398649     74.216049     70.270855     36.170209     16.015211   
min        0.000000      7.045357      5.992488      0.000000      3.794128   
25%        1.000000     47.854000     38.850000     18.107336     19.771846   
50%        2.000000     84.121000     67.250128     53.860009     29.001860   
75%        3.000000    139.601499    118.195925     87.766690     42.248642   
max        4.000000    553.847998    524.565884    100.000000    100.000000   

         close_75_z            ao           vix    turbulence  
count  95990.000000  95990.000000  95990.000000  95990.000000  
mean       0.417570      0.542043     18.721163     34.943606  
std        1.337794      5.719594      7.269653     43.065944  
min       -5.414782   -159.193413      9.140000      0.000000  
25%       -0.571311     -1.110588     13.630000     14.972940  
50%        0.635934      0.488779     16.875000     24.175838  
75%        1.457174      2.307581     21.760000     40.000708  
max        5.784537     62.724292     82.690002    652.614185

Split Train and Test datasets

In [27]:
train = data_split(processed_full, TRAIN_START_DATE,TRAIN_END_DATE)
train

date   tic        open        high         low       close  \
0     2010-01-04  AAPL    7.622500    7.660714    7.585000    6.470740   
0     2010-01-04  AMGN   56.630001   57.869999   56.560001   41.200798   
0     2010-01-04   AXP   40.810001   41.099998   40.389999   33.090435   
0     2010-01-04    BA   55.720001   56.389999   54.799999   43.777542   
0     2010-01-04   CAT   57.650002   59.189999   57.509998   40.190224   
...          ...   ...         ...         ...         ...         ...   
2956  2021-09-30   UNH  401.489990  403.489990  390.459991  375.759796   
2956  2021-09-30     V  227.580002  228.789993  222.630005  218.139236   
2956  2021-09-30    VZ   54.500000   54.509998   54.000000   45.622715   
2956  2021-09-30   WBA   48.790001   48.930000   46.919998   40.519119   
2956  2021-09-30   WMT   46.880001   47.243332   46.416668   44.566536   

           volume  day  high_5_sma        boll   stochrsi         adx  \
0     493729600.0  0.0    7.660714    6.470740   0.000000  100.000000   
0       5277400.0  0.0   57.869999   41.200798   0.000000  100.000000   
0       6894300.0  0.0   41.099998   33.090435   0.000000  100.000000   
0       6186700.0  0.0   56.389999   43.777542   0.000000  100.000000   
0       7325600.0  0.0   59.189999   40.190224   0.000000  100.000000   
...           ...  ...         ...         ...        ...         ...   
2956    3779900.0  3.0  405.876001  395.233066   0.000000   43.119455   
2956    7128500.0  3.0  230.391998  220.443531  41.471493   18.111203   
2956   18736600.0  3.0   54.616000   46.019304  40.008441   19.555807   
2956    6449400.0  3.0   49.336000   42.461536   0.000000   22.552841   
2956   22457700.0  3.0   47.524667   46.131387   0.000000   60.748329   

      close_75_z         ao        vix  turbulence  
0       0.000000   0.000000  20.040001    0.000000  
0       0.000000   0.000000  20.040001    0.000000  
0       0.000000   0.000000  20.040001    0.000000  
0       0.000000   0.000000  20.040001    0.000000  
0       0.000000   0.000000  20.040001    0.000000  
...          ...        ...        ...         ...  
2956   -2.318633 -12.985296  23.139999   24.927423  
2956   -1.507286  -0.069471  23.139999   24.927423  
2956   -1.993537  -0.480236  23.139999   24.927423  
2956   -0.751808  -0.581059  23.139999   24.927423  
2956   -0.878288  -1.592608  23.139999   24.927423  

[85753 rows x 16 columns]

In [28]:
len(train.tic.unique())

29

In [29]:
train.tic.unique()

array(['AAPL', 'AMGN', 'AXP', 'BA', 'CAT', 'CRM', 'CSCO', 'CVX', 'DIS',
       'GS', 'HD', 'HON', 'IBM', 'INTC', 'JNJ', 'JPM', 'KO', 'MCD', 'MMM',
       'MRK', 'MSFT', 'NKE', 'PG', 'TRV', 'UNH', 'V', 'VZ', 'WBA', 'WMT'],
      dtype=object)

In [30]:
trade = data_split(processed_full, TEST_START_DATE,TEST_END_DATE)
trade

date   tic        open        high         low       close  \
0    2021-10-01  AAPL  141.899994  142.919998  139.110001  140.653488   
0    2021-10-01  AMGN  213.589996  214.610001  210.800003  195.822235   
0    2021-10-01   AXP  168.500000  175.119995  168.479996  167.727432   
0    2021-10-01    BA  222.850006  226.720001  220.600006  226.000000   
0    2021-10-01   CAT  192.899994  195.869995  191.240005  183.513992   
..          ...   ...         ...         ...         ...         ...   
352  2023-02-27   UNH  488.769989  490.940002  481.959991  472.278198   
352  2023-02-27     V  220.729996  221.440002  219.339996  218.230591   
352  2023-02-27    VZ   38.990002   39.150002   38.630001   35.602486   
352  2023-02-27   WBA   36.049999   36.080002   35.270000   32.621925   
352  2023-02-27   WMT   47.570000   47.696667   46.886665   46.121086   

         volume  day  high_5_sma        boll   stochrsi        adx  \
0    94639600.0  4.0  144.492001  145.480988  36.066167  51.586046   
0     2629400.0  4.0  215.557999  197.962447  75.148849  33.147887   
0     3956000.0  4.0  175.300000  159.502592  65.456038  23.039918   
0     9113600.0  4.0  227.198001  216.318501  95.477772  13.576357   
0     3695500.0  4.0  199.956000  189.037464  66.701625  33.844287   
..          ...  ...         ...         ...        ...        ...   
352   3006200.0  0.0  494.414001  476.145312  32.661437  11.867177   
352   4255300.0  0.0  221.592001  224.423517   7.819466  41.614291   
352  14210900.0  0.0   39.360000   36.881721  26.473435  40.124667   
352   5580100.0  0.0   36.282000   33.398429   2.329875  26.347004   
352  16647300.0  0.0   48.407333   46.782871  15.558425  24.757027   

     close_75_z        ao        vix  turbulence  
0     -0.448095 -5.508792  21.100000  120.031195  
0     -1.460555 -6.445471  21.100000  120.031195  
0      1.450819  8.481735  21.100000  120.031195  
0      0.034531  6.024826  21.100000  120.031195  
0     -2.043575 -7.286470  21.100000  120.031195  
..          ...       ...        ...         ...  
352   -1.131985  1.691383  20.950001    7.163887  
352    0.455638 -4.844647  20.950001    7.163887  
352   -0.081318 -1.411559  20.950001    7.163887  
352   -1.184411 -0.406441  20.950001    7.163887  
352   -0.969926 -0.022863  20.950001    7.163887  

[10237 rows x 16 columns]

In [31]:
train_length = len(train)
trade_length = len(trade)
print("Number of training samples: ", train_length)
print("Number of testing samples", trade_length)

Number of training samples:  85753
Number of testing samples 10237


In [32]:
train.tail()

date  tic        open        high         low       close  \
2956  2021-09-30  UNH  401.489990  403.489990  390.459991  375.759796   
2956  2021-09-30    V  227.580002  228.789993  222.630005  218.139236   
2956  2021-09-30   VZ   54.500000   54.509998   54.000000   45.622715   
2956  2021-09-30  WBA   48.790001   48.930000   46.919998   40.519119   
2956  2021-09-30  WMT   46.880001   47.243332   46.416668   44.566536   

          volume  day  high_5_sma        boll   stochrsi        adx  \
2956   3779900.0  3.0  405.876001  395.233066   0.000000  43.119455   
2956   7128500.0  3.0  230.391998  220.443531  41.471493  18.111203   
2956  18736600.0  3.0   54.616000   46.019304  40.008441  19.555807   
2956   6449400.0  3.0   49.336000   42.461536   0.000000  22.552841   
2956  22457700.0  3.0   47.524667   46.131387   0.000000  60.748329   

      close_75_z         ao        vix  turbulence  
2956   -2.318633 -12.985296  23.139999   24.927423  
2956   -1.507286  -0.069471  23.139999   24.927423  
2956   -1.993537  -0.480236  23.139999   24.927423  
2956   -0.751808  -0.581059  23.139999   24.927423  
2956   -0.878288  -1.592608  23.139999   24.927423

In [33]:
trade.head()

date   tic        open        high         low       close  \
0  2021-10-01  AAPL  141.899994  142.919998  139.110001  140.653488   
0  2021-10-01  AMGN  213.589996  214.610001  210.800003  195.822235   
0  2021-10-01   AXP  168.500000  175.119995  168.479996  167.727432   
0  2021-10-01    BA  222.850006  226.720001  220.600006  226.000000   
0  2021-10-01   CAT  192.899994  195.869995  191.240005  183.513992   

       volume  day  high_5_sma        boll   stochrsi        adx  close_75_z  \
0  94639600.0  4.0  144.492001  145.480988  36.066167  51.586046   -0.448095   
0   2629400.0  4.0  215.557999  197.962447  75.148849  33.147887   -1.460555   
0   3956000.0  4.0  175.300000  159.502592  65.456038  23.039918    1.450819   
0   9113600.0  4.0  227.198001  216.318501  95.477772  13.576357    0.034531   
0   3695500.0  4.0  199.956000  189.037464  66.701625  33.844287   -2.043575   

         ao   vix  turbulence  
0 -5.508792  21.1  120.031195  
0 -6.445471  21.1  120.031195  
0  8.481735  21.1  120.031195  
0  6.024826  21.1  120.031195  
0 -7.286470  21.1  120.031195

Since we need to set the parameters for the environment functions, we need to compute the stock dimension and state space.

In [34]:
# Number of unique stocks used for the training 
stock_dimension = len(train.tic.unique())
# {balance, close price, shares, N-technical indicators}
# Balance will occupy 1 input node, and it is computed as: balance = balance (t) − amount of money we pay to buy shares + amount of money we receive to sell shares
# We will have N input nodes for the stock prices and N additional input nodes to indicate the current number of shares for each stock --> 2*N
# we will have one node for every technical indicator for every stock --> M indicators * N stocks
state_space = 1 + 2*stock_dimension + len(INDICATORS)*stock_dimension
print(f"Stock Dimension (Number of different companies in which we want to invest initially): {stock_dimension}, State Space (Number of input nodes to feed to the network): {state_space}")

Stock Dimension (Number of different companies in which we want to invest initially): 29, State Space (Number of input nodes to feed to the network): 233


Most of the trading companies demand trading commissions or costs. Here, we will simulate a buying and selling commission of 0,1% for each transaction. We will assume the user starts having no shares of any stock. Let's also assume we have 1.000.000 dollars to invest with. We will also define a parameter that sets the maximum amount of shares to trade, h_max. It is interesting to set the scaling reward or gamma (importance we give to the future reward), so that we specify if we give more importance to the short or long term. We could modify these parameters, if needed.

In [35]:
buy_cost_list = sell_cost_list = [0.001] * stock_dimension
num_stock_shares = [0] * stock_dimension
h_max = 100
initial_amount = 1000000
gamma = 1e-4 # we are assuming we want to get the highest return in the short term, preventing ourselves from the risk and uncertainty caused by external factors in the long term

HAZ PRUEBAS CON UN GAMMA MÁS ALTO

Let's set the configuration that will be passed to the Environment class

In [36]:
env_kwargs = {
    "hmax": h_max,
    "initial_amount": initial_amount, 
    "num_stock_shares": num_stock_shares,
    "buy_cost_pct": buy_cost_list,
    "sell_cost_pct": sell_cost_list,
    "state_space": state_space,
    "stock_dim": stock_dimension,
    "tech_indicator_list": INDICATORS,
    "action_space": stock_dimension,
    "reward_scaling": gamma
}

Let's create the Stock Trading Environment!

In [37]:
e_train_gym = StockTradingEnv(df = train, **env_kwargs) # creates instance of the Environment class
print("Environment class type", type(e_train_gym))
env_train, _ = e_train_gym.get_sb_env() # resets the environment and converts the initial environment into a DummyVecEnv instance
print("External Environment class type: ", type(env_train))

Environment class type <class 'finrl.meta.env_stock_trading.env_stocktrading.StockTradingEnv'>
External Environment class type:  <class 'stable_baselines3.common.vec_env.dummy_vec_env.DummyVecEnv'>


Since we will use different RL algorithms, let's set some flags:

In [38]:
if_using_a2c = True
if_using_ddpg = True
if_using_ppo = True
if_using_td3 = True
if_using_sac = True

Let's create the Deep Reinforcement Learning Agent!

podríamos runear todos los ind (p.e. 3 o 4 ind) y con los mejores, cambiar el resto de parametros (fechas, gamma,...)

# A2C

In [39]:
agent = DRLAgent(env = env_train) # creates Agent instance
model_a2c = agent.get_model("a2c") # gets stablebaselines3 model  

if if_using_a2c: # where to store the results
  # set up logger
  tmp_path = 'resultadosTFG' + '/set_1+' + '/a2c'
  new_logger_a2c = configure(tmp_path, ["stdout", "csv", "tensorboard"])
  # Set new logger
  model_a2c.set_logger(new_logger_a2c)

{'n_steps': 5, 'ent_coef': 0.01, 'learning_rate': 0.0007}
Using cpu device


Logging to resultadosTFG/set_1+/a2c


Let's train the agent!

In [40]:
trained_a2c = agent.train_model(model=model_a2c, 
                             tb_log_name='a2c',
                             total_timesteps=50000) if if_using_a2c else None

--------------------------------------
| time/                 |            |
|    fps                | 191        |
|    iterations         | 100        |
|    time_elapsed       | 2          |
|    total_timesteps    | 500        |
| train/                |            |
|    entropy_loss       | -41.2      |
|    explained_variance | 0          |
|    learning_rate      | 0.0007     |
|    n_updates          | 99         |
|    policy_loss        | -38.1      |
|    reward             | -1.4389844 |
|    std                | 1          |
|    value_loss         | 1.21       |
--------------------------------------
---------------------------------------
| time/                 |             |
|    fps                | 184         |
|    iterations         | 200         |
|    time_elapsed       | 5           |
|    total_timesteps    | 1000        |
| train/                |             |
|    entropy_loss       | -41.2       |
|    explained_variance | 0           |
|    learning_ra

In [41]:
trained_a2c.policy

ActorCriticPolicy(
  (features_extractor): FlattenExtractor(
    (flatten): Flatten(start_dim=1, end_dim=-1)
  )
  (pi_features_extractor): FlattenExtractor(
    (flatten): Flatten(start_dim=1, end_dim=-1)
  )
  (vf_features_extractor): FlattenExtractor(
    (flatten): Flatten(start_dim=1, end_dim=-1)
  )
  (mlp_extractor): MlpExtractor(
    (policy_net): Sequential(
      (0): Linear(in_features=233, out_features=64, bias=True)
      (1): Tanh()
      (2): Linear(in_features=64, out_features=64, bias=True)
      (3): Tanh()
    )
    (value_net): Sequential(
      (0): Linear(in_features=233, out_features=64, bias=True)
      (1): Tanh()
      (2): Linear(in_features=64, out_features=64, bias=True)
      (3): Tanh()
    )
  )
  (action_net): Linear(in_features=64, out_features=29, bias=True)
  (value_net): Linear(in_features=64, out_features=1, bias=True)
)

Let's see the learning progress of the agent

In [42]:
learning_process = pd.read_csv("resultadosTFG/set_1+/a2c/progress.csv")
learning_process

train/entropy_loss  train/value_loss  train/learning_rate  train/reward  \
0           -41.240517          1.205716               0.0007     -1.438984   
1           -41.249054          2.062591               0.0007     -0.248798   
2           -41.280807          6.674653               0.0007     -3.659865   
3           -41.326515          1.694329               0.0007      0.439979   
4           -41.375134          4.119524               0.0007     -1.161251   
..                 ...               ...                  ...           ...   
95          -43.409382          1.324000               0.0007     -1.547008   
96          -43.425140          0.699479               0.0007     -1.301031   
97          -43.477711         23.147018               0.0007     -1.318651   
98          -43.497223          4.537453               0.0007      2.912987   
99          -43.496784          9.342154               0.0007     -7.202511   

    train/explained_variance  time/iterations  time/time_elapsed  \
0               0.000000e+00              100                  2   
1               0.000000e+00              200                  5   
2               0.000000e+00              300                  8   
3               0.000000e+00              400                 10   
4               5.960464e-08              500                 13   
..                       ...              ...                ...   
95              0.000000e+00             9600                275   
96              1.788139e-07             9700                278   
97              0.000000e+00             9800                281   
98              1.192093e-07             9900                284   
99              0.000000e+00            10000                287   

    train/policy_loss  time/total_timesteps  train/std  time/fps  \
0          -38.097248                   500   1.003585       191   
1          -50.094307                  1000   1.003422       184   
2          -58.460236                  1500   1.004764       187   
3          -41.661301                  2000   1.006623       187   
4          -77.430893                  2500   1.008214       187   
..                ...                   ...        ...       ...   
95          18.181538                 48000   1.083270       174   
96          -6.290329                 48500   1.083888       174   
97        -201.329071                 49000   1.085819       174   
98         -18.289780                 49500   1.086395       174   
99        -125.689430                 50000   1.086470       174   

    train/n_updates  
0                99  
1               199  
2               299  
3               399  
4               499  
..              ...  
95             9599  
96             9699  
97             9799  
98             9899  
99             9999  

[100 rows x 12 columns]

Plot the training results

In [43]:
def plot_metrics(df, n_rows, n_cols):
    fig, axes = plt.subplots(nrows=n_rows, ncols=n_cols, figsize=(5 * n_cols, 5 * n_rows))
    axes = axes.flatten()  # Flatten the array of axes if more than one row or column

    # List of tuples containing (y-axis, title)
    metrics = [
        ('train/reward', 'Reward'),
        ('train/policy_loss', 'Policy Loss'),
        ('train/std', 'Standard Deviation'),
        ('train/n_updates', 'Number of Updates'),
        ('train/value_loss', 'Value Loss'),
        ('time/fps', 'Frames Per Second'),
        ('train/explained_variance', 'Explained Variance'),
        ('train/entropy_loss', 'Entropy Loss')
    ]

    # Plot each metric
    for ax, (metric, title) in zip(axes, metrics):
        ax.plot(df['time/total_timesteps'], df[metric], label=title)
        ax.set_xlabel('Total Timesteps')
        ax.set_ylabel(title)
        ax.set_title(title)
        ax.grid(True)
        ax.legend()

    plt.tight_layout()
    plt.savefig(f'resultadosTFG/set_1+/a2c/trainingStatsResults.png')
    plt.close()

df = learning_process
plot_metrics(df, n_rows=4, n_cols=2)  # Modify n_rows and n_cols as needed


The agent is not learning very well... 

Podríamos hacer una tabla resumen de todos los algos y pones cuántos steps han sido necesarios, la LR de cada uno, etc

# PPO

Set PPO parameters and set the logger

In [44]:
agent = DRLAgent(env = env_train)
PPO_PARAMS = {
    "n_steps": 2048,
    "ent_coef": 0.01,
    "learning_rate": 0.00025,
    "batch_size": 128,
}
model_ppo = agent.get_model("ppo",model_kwargs = PPO_PARAMS)

if if_using_ppo:
  # set up logger
  tmp_path = 'resultadosTFG' + '/set_1+' + '/ppo'
  new_logger_ppo = configure(tmp_path, ["stdout", "csv", "tensorboard"])
  # Set new logger
  model_ppo.set_logger(new_logger_ppo)

{'n_steps': 2048, 'ent_coef': 0.01, 'learning_rate': 0.00025, 'batch_size': 128}
Using cpu device
Logging to resultadosTFG/set_1+/ppo


Train PPO

In [45]:
trained_ppo = agent.train_model(model=model_ppo, 
                             tb_log_name='ppo',
                             total_timesteps=50000) if if_using_ppo else None

-------------------------------------
| time/              |              |
|    fps             | 214          |
|    iterations      | 1            |
|    time_elapsed    | 9            |
|    total_timesteps | 2048         |
| train/             |              |
|    reward          | -0.036239117 |
-------------------------------------
----------------------------------------
| time/                   |            |
|    fps                  | 213        |
|    iterations           | 2          |
|    time_elapsed         | 19         |
|    total_timesteps      | 4096       |
| train/                  |            |
|    approx_kl            | 0.01862812 |
|    clip_fraction        | 0.199      |
|    clip_range           | 0.2        |
|    entropy_loss         | -41.2      |
|    explained_variance   | -0.0147    |
|    learning_rate        | 0.00025    |
|    loss                 | 5.94       |
|    n_updates            | 10         |
|    policy_gradient_loss | -0.0264    |
| 

In [46]:
trained_ppo.policy

ActorCriticPolicy(
  (features_extractor): FlattenExtractor(
    (flatten): Flatten(start_dim=1, end_dim=-1)
  )
  (pi_features_extractor): FlattenExtractor(
    (flatten): Flatten(start_dim=1, end_dim=-1)
  )
  (vf_features_extractor): FlattenExtractor(
    (flatten): Flatten(start_dim=1, end_dim=-1)
  )
  (mlp_extractor): MlpExtractor(
    (policy_net): Sequential(
      (0): Linear(in_features=233, out_features=64, bias=True)
      (1): Tanh()
      (2): Linear(in_features=64, out_features=64, bias=True)
      (3): Tanh()
    )
    (value_net): Sequential(
      (0): Linear(in_features=233, out_features=64, bias=True)
      (1): Tanh()
      (2): Linear(in_features=64, out_features=64, bias=True)
      (3): Tanh()
    )
  )
  (action_net): Linear(in_features=64, out_features=29, bias=True)
  (value_net): Linear(in_features=64, out_features=1, bias=True)
)

Let's see the learning progress of the agent

In [47]:
learning_process = pd.read_csv("resultadosTFG/set_1+/ppo/progress.csv")
learning_process

time/time_elapsed  time/total_timesteps  train/reward  time/iterations  \
0                   9                  2048     -0.036239                1   
1                  19                  4096     -0.334981                2   
2                  28                  6144      1.113413                3   
3                  38                  8192      0.588559                4   
4                  48                 10240     -1.852411                5   
5                  58                 12288     -0.035900                6   
6                  67                 14336      1.742324                7   
7                  77                 16384     -2.167161                8   
8                  87                 18432      0.955363                9   
9                  96                 20480     -0.888016               10   
10                105                 22528     -0.634882               11   
11                115                 24576      0.736658               12   
12                125                 26624     -0.118615               13   
13                134                 28672      4.992110               14   
14                144                 30720      1.672049               15   
15                153                 32768      0.424115               16   
16                163                 34816     -7.010513               17   
17                173                 36864     -5.029840               18   
18                182                 38912     -0.048997               19   
19                192                 40960      1.272094               20   
20                202                 43008      0.147026               21   
21                211                 45056     -0.141118               22   
22                221                 47104      1.512402               23   
23                230                 49152     -0.293348               24   
24                240                 51200      2.426810               25   

    time/fps  train/entropy_loss  train/policy_gradient_loss  \
0        214                 NaN                         NaN   
1        213          -41.174872                   -0.026413   
2        213          -41.211647                   -0.020435   
3        212          -41.237934                   -0.020320   
4        212          -41.279009                   -0.028819   
5        211          -41.355904                   -0.021363   
6        211          -41.407987                   -0.010248   
7        211          -41.456901                   -0.024262   
8        211          -41.547670                   -0.014947   
9        212          -41.626488                   -0.019007   
10       212          -41.691560                   -0.016806   
11       212          -41.751117                   -0.024825   
12       212          -41.774607                   -0.012592   
13       212          -41.832640                   -0.019901   
14       212          -41.897540                   -0.017111   
15       212          -41.937538                   -0.014472   
16       212          -41.963613                   -0.014819   
17       212          -41.973871                   -0.012179   
18       212          -42.028780                   -0.017984   
19       212          -42.110917                   -0.005957   
20       212          -42.142399                   -0.013292   
21       212          -42.156062                   -0.015206   
22       212          -42.174626                   -0.010380   
23       212          -42.205524                   -0.014944   
24       212          -42.253886                   -0.020789   

    train/value_loss  train/loss  train/explained_variance  train/n_updates  \
0                NaN         NaN                       NaN              NaN   
1           9.996573    5.939942                 -0.014661             10.0   
2          41.299626   30.586464                 -0.008900             20

Plot the training results

In [48]:
def plot_metrics(df, n_rows, n_cols):
    fig, axes = plt.subplots(nrows=n_rows, ncols=n_cols, figsize=(5 * n_cols, 5 * n_rows))
    axes = axes.flatten()  # Flatten the array of axes if more than one row or column

    metrics = [
        ('train/reward', 'Reward'),
        ('train/loss', 'Loss'),
        ('train/std', 'Standard Deviation'),
        ('train/approx_kl', 'approximate Kullback-Leibler divergence'),
        ('train/clip_fraction', 'Clip Fraction'),
        ('train/clip_range', 'Clip Range'),
        ('train/explained_variance', 'Explained Variance'),
        ('train/value_loss', 'Value Loss'),
        ('train/policy_gradient_loss', 'Policy Gradient Loss'),
        ('train/entropy_loss', 'Entropy Loss')
    ]

    # Plot each metric
    for ax, (metric, title) in zip(axes, metrics):
        ax.plot(df['time/total_timesteps'], df[metric], label=title)
        ax.set_xlabel('Total Timesteps')
        ax.set_ylabel(title)
        ax.set_title(title)
        ax.grid(True)
        ax.legend()

    plt.tight_layout()
    plt.savefig(f'resultadosTFG/set_1+/ppo/trainingStatsResults.png')
    plt.close()

df = learning_process
plot_metrics(df, n_rows=5, n_cols=2)  # Modify n_rows and n_cols as needed

# DDPG

Create the agent and set the logger

In [49]:
agent = DRLAgent(env = env_train)
model_ddpg = agent.get_model("ddpg")

if if_using_ddpg:
  # set up logger
  tmp_path = 'resultadosTFG' + '/set_1+' + '/ddpg'
  new_logger_ddpg = configure(tmp_path, ["stdout", "csv", "tensorboard"])
  # Set new logger
  model_ddpg.set_logger(new_logger_ddpg)

{'batch_size': 128, 'buffer_size': 50000, 'learning_rate': 0.001}
Using cpu device
Logging to resultadosTFG/set_1+/ddpg


Train the agent

In [50]:
trained_ddpg = agent.train_model(model=model_ddpg, 
                             tb_log_name='ddpg',
                             total_timesteps=50000) if if_using_ddpg else None

day: 2956, episode: 40
begin_total_asset: 1000000.00
end_total_asset: 4515716.40
total_reward: 3515716.40
total_cost: 1091.13
total_trades: 44357
Sharpe: 0.796
----------------------------------
| time/              |           |
|    episodes        | 4         |
|    fps             | 118       |
|    time_elapsed    | 99        |
|    total_timesteps | 11828     |
| train/             |           |
|    actor_loss      | -20.2     |
|    critic_loss     | 152       |
|    learning_rate   | 0.001     |
|    n_updates       | 8871      |
|    reward          | -7.923421 |
----------------------------------
----------------------------------
| time/              |           |
|    episodes        | 8         |
|    fps             | 107       |
|    time_elapsed    | 220       |
|    total_timesteps | 23656     |
| train/             |           |
|    actor_loss      | -4.57     |
|    critic_loss     | 5.6       |
|    learning_rate   | 0.001     |
|    n_updates       | 20699     |


In [51]:
trained_ddpg.policy

TD3Policy(
  (actor): Actor(
    (features_extractor): FlattenExtractor(
      (flatten): Flatten(start_dim=1, end_dim=-1)
    )
    (mu): Sequential(
      (0): Linear(in_features=233, out_features=400, bias=True)
      (1): ReLU()
      (2): Linear(in_features=400, out_features=300, bias=True)
      (3): ReLU()
      (4): Linear(in_features=300, out_features=29, bias=True)
      (5): Tanh()
    )
  )
  (actor_target): Actor(
    (features_extractor): FlattenExtractor(
      (flatten): Flatten(start_dim=1, end_dim=-1)
    )
    (mu): Sequential(
      (0): Linear(in_features=233, out_features=400, bias=True)
      (1): ReLU()
      (2): Linear(in_features=400, out_features=300, bias=True)
      (3): ReLU()
      (4): Linear(in_features=300, out_features=29, bias=True)
      (5): Tanh()
    )
  )
  (critic): ContinuousCritic(
    (features_extractor): FlattenExtractor(
      (flatten): Flatten(start_dim=1, end_dim=-1)
    )
    (qf0): Sequential(
      (0): Linear(in_features=262, out_

Let's see the learning progress of the agent 

In [52]:
learning_process = pd.read_csv("resultadosTFG/set_1+/ddpg/progress.csv")
learning_process

train/learning_rate  train/reward  time/episodes  time/time_elapsed  \
0                0.001     -7.923421              4                 99   
1                0.001     -7.923421              8                220   
2                0.001     -7.923421             12                355   
3                0.001     -7.923421             16                483   

   train/critic_loss  train/actor_loss  time/total_timesteps  time/fps  \
0         151.806874        -20.221725                 11828       118   
1           5.603054         -4.571850                 23656       107   
2           3.566984         -5.955121                 35484        99   
3           1.907140         -8.116841                 47312        97   

   train/n_updates  
0             8871  
1            20699  
2            32527  
3            44355

Plot the results of the training

In [53]:
def plot_metrics(df, n_rows, n_cols):
    fig, axes = plt.subplots(nrows=n_rows, ncols=n_cols, figsize=(5 * n_cols, 5 * n_rows))
    axes = axes.flatten()  # Flatten the array of axes if more than one row or column

    metrics = [
        ('train/reward', 'Reward'),
        ('train/actor_loss', 'Actor Loss'),
        ('train/n_updates', 'Number of Updates'),
        ('train/critic_loss', 'Critic Loss')
    ]

    # Plot each metric
    for ax, (metric, title) in zip(axes, metrics):
        ax.plot(df['time/total_timesteps'], df[metric], label=title)
        ax.set_xlabel('Total Timesteps')
        ax.set_ylabel(title)
        ax.set_title(title)
        ax.grid(True)
        ax.legend()

    plt.tight_layout()
    plt.savefig(f'resultadosTFG/set_1+/ddpg/trainingStatsResults.png')
    plt.close()

df = learning_process
plot_metrics(df, n_rows=4, n_cols=1)  # Modify n_rows and n_cols as needed

# TD3

Create the agent and set the logger

In [54]:
agent = DRLAgent(env = env_train)
TD3_PARAMS = {"batch_size": 100, 
              "buffer_size": 1000000, 
              "learning_rate": 0.001}

model_td3 = agent.get_model("td3",model_kwargs = TD3_PARAMS)

if if_using_td3:
  # set up logger
  tmp_path = 'resultadosTFG' + '/set_1+' + '/td3'
  new_logger_td3 = configure(tmp_path, ["stdout", "csv", "tensorboard"])
  # Set new logger
  model_td3.set_logger(new_logger_td3)

{'batch_size': 100, 'buffer_size': 1000000, 'learning_rate': 0.001}
Using cpu device
Logging to resultadosTFG/set_1+/td3


/Users/carolinaalbamaruganrubio/miniforge3/envs/ai4finance/lib/python3.10/site-packages/stable_baselines3/common/buffers.py:241: UserWarning: This system does not have apparently enough memory to store the complete replay buffer 1.99GB > 1.22GB
  warnings.warn(


Train TD3

In [55]:
trained_td3 = agent.train_model(model=model_td3, 
                             tb_log_name='td3',
                             total_timesteps=50000) if if_using_td3 else None

----------------------------------
| time/              |           |
|    episodes        | 4         |
|    fps             | 110       |
|    time_elapsed    | 107       |
|    total_timesteps | 11828     |
| train/             |           |
|    actor_loss      | 62.5      |
|    critic_loss     | 2.1e+03   |
|    learning_rate   | 0.001     |
|    n_updates       | 8871      |
|    reward          | -10.01565 |
----------------------------------
day: 2956, episode: 60
begin_total_asset: 1000000.00
end_total_asset: 5569243.22
total_reward: 4569243.22
total_cost: 1120.26
total_trades: 41408
Sharpe: 0.864
----------------------------------
| time/              |           |
|    episodes        | 8         |
|    fps             | 101       |
|    time_elapsed    | 232       |
|    total_timesteps | 23656     |
| train/             |           |
|    actor_loss      | 18.2      |
|    critic_loss     | 379       |
|    learning_rate   | 0.001     |
|    n_updates       | 20699     |


In [56]:
trained_td3.policy

TD3Policy(
  (actor): Actor(
    (features_extractor): FlattenExtractor(
      (flatten): Flatten(start_dim=1, end_dim=-1)
    )
    (mu): Sequential(
      (0): Linear(in_features=233, out_features=400, bias=True)
      (1): ReLU()
      (2): Linear(in_features=400, out_features=300, bias=True)
      (3): ReLU()
      (4): Linear(in_features=300, out_features=29, bias=True)
      (5): Tanh()
    )
  )
  (actor_target): Actor(
    (features_extractor): FlattenExtractor(
      (flatten): Flatten(start_dim=1, end_dim=-1)
    )
    (mu): Sequential(
      (0): Linear(in_features=233, out_features=400, bias=True)
      (1): ReLU()
      (2): Linear(in_features=400, out_features=300, bias=True)
      (3): ReLU()
      (4): Linear(in_features=300, out_features=29, bias=True)
      (5): Tanh()
    )
  )
  (critic): ContinuousCritic(
    (features_extractor): FlattenExtractor(
      (flatten): Flatten(start_dim=1, end_dim=-1)
    )
    (qf0): Sequential(
      (0): Linear(in_features=262, out_

Let's see agent's learning process

In [57]:
learning_process = pd.read_csv("resultadosTFG/set_1+/td3/progress.csv")
learning_process

train/learning_rate  train/reward  time/episodes  time/time_elapsed  \
0                0.001     -10.01565              4                107   
1                0.001     -10.01565              8                232   
2                0.001     -10.01565             12                356   
3                0.001     -10.01565             16                488   

   train/critic_loss  train/actor_loss  time/total_timesteps  time/fps  \
0        2095.474600         62.494131                 11828       110   
1         379.398785         18.221741                 23656       101   
2          45.153934         13.591354                 35484        99   
3          35.692630         16.944116                 47312        96   

   train/n_updates  
0             8871  
1            20699  
2            32527  
3            44355

Plot training results

In [58]:
def plot_metrics(df, n_rows, n_cols):
    fig, axes = plt.subplots(nrows=n_rows, ncols=n_cols, figsize=(5 * n_cols, 5 * n_rows))
    axes = axes.flatten()  # Flatten the array of axes if more than one row or column

    metrics = [
        ('train/reward', 'Reward'),
        ('train/actor_loss', 'Actor Loss'),
        ('train/n_updates', 'Number of Updates'),
        ('train/critic_loss', 'Critic Loss')
    ]

    # Plot each metric
    for ax, (metric, title) in zip(axes, metrics):
        ax.plot(df['time/total_timesteps'], df[metric], label=title)
        ax.set_xlabel('Total Timesteps')
        ax.set_ylabel(title)
        ax.set_title(title)
        ax.grid(True)
        ax.legend()

    plt.tight_layout()
    plt.savefig(f'resultadosTFG/set_1+/td3/trainingStatsResults.png')
    plt.close()

df = learning_process
plot_metrics(df, n_rows=4, n_cols=1)  # Modify n_rows and n_cols as needed

# SAC

Create the agent, set parameters for training, and set logger

In [59]:
agent = DRLAgent(env = env_train)
SAC_PARAMS = {
    "batch_size": 128,
    "buffer_size": 100000,
    "learning_rate": 0.0001,
    "learning_starts": 100,
    "ent_coef": "auto_0.1",
}

model_sac = agent.get_model("sac",model_kwargs = SAC_PARAMS)

if if_using_sac:
  # set up logger
  tmp_path = 'resultadosTFG' + '/set_1+' + '/sac'
  new_logger_sac = configure(tmp_path, ["stdout", "csv", "tensorboard"])
  # Set new logger
  model_sac.set_logger(new_logger_sac)

{'batch_size': 128, 'buffer_size': 100000, 'learning_rate': 0.0001, 'learning_starts': 100, 'ent_coef': 'auto_0.1'}
Using cpu device
Logging to resultadosTFG/set_1+/sac


Train SAC

In [60]:
trained_sac = agent.train_model(model=model_sac, 
                             tb_log_name='sac',
                             total_timesteps=50000) if if_using_sac else None

----------------------------------
| time/              |           |
|    episodes        | 4         |
|    fps             | 74        |
|    time_elapsed    | 158       |
|    total_timesteps | 11828     |
| train/             |           |
|    actor_loss      | 1.94e+03  |
|    critic_loss     | 4.12e+03  |
|    ent_coef        | 0.277     |
|    ent_coef_loss   | -13.7     |
|    learning_rate   | 0.0001    |
|    n_updates       | 11727     |
|    reward          | -7.788928 |
----------------------------------
day: 2956, episode: 80
begin_total_asset: 1000000.00
end_total_asset: 4815454.28
total_reward: 3815454.28
total_cost: 11020.12
total_trades: 49481
Sharpe: 0.797
----------------------------------
| time/              |           |
|    episodes        | 8         |
|    fps             | 69        |
|    time_elapsed    | 338       |
|    total_timesteps | 23656     |
| train/             |           |
|    actor_loss      | 747       |
|    critic_loss     | 76.3      |

In [61]:
trained_sac.policy

SACPolicy(
  (actor): Actor(
    (features_extractor): FlattenExtractor(
      (flatten): Flatten(start_dim=1, end_dim=-1)
    )
    (latent_pi): Sequential(
      (0): Linear(in_features=233, out_features=256, bias=True)
      (1): ReLU()
      (2): Linear(in_features=256, out_features=256, bias=True)
      (3): ReLU()
    )
    (mu): Linear(in_features=256, out_features=29, bias=True)
    (log_std): Linear(in_features=256, out_features=29, bias=True)
  )
  (critic): ContinuousCritic(
    (features_extractor): FlattenExtractor(
      (flatten): Flatten(start_dim=1, end_dim=-1)
    )
    (qf0): Sequential(
      (0): Linear(in_features=262, out_features=256, bias=True)
      (1): ReLU()
      (2): Linear(in_features=256, out_features=256, bias=True)
      (3): ReLU()
      (4): Linear(in_features=256, out_features=1, bias=True)
    )
    (qf1): Sequential(
      (0): Linear(in_features=262, out_features=256, bias=True)
      (1): ReLU()
      (2): Linear(in_features=256, out_features=2

Let's see agent's learning process

In [62]:
learning_process = pd.read_csv("resultadosTFG/set_1+/sac/progress.csv")
learning_process

train/learning_rate  train/reward  time/episodes  train/ent_coef  \
0               0.0001     -7.788928              4        0.277283   
1               0.0001     -6.597044              8        0.094807   
2               0.0001     -7.519960             12        0.030434   
3               0.0001     -7.573848             16        0.010011   

   time/time_elapsed  train/critic_loss  train/actor_loss  \
0                158        4124.739258       1936.786865   
1                338          76.335602        747.340210   
2                522          59.005867        319.834320   
3                707          54.817741        163.283554   

   time/total_timesteps  time/fps  train/ent_coef_loss  train/n_updates  
0                 11828        74           -13.694695            11727  
1                 23656        69           -84.926376            23555  
2                 35484        67           -81.185020            35383  
3                 47312        66           -51.255726            47211

Agent's training results

In [63]:
def plot_metrics(df, n_rows, n_cols):
    fig, axes = plt.subplots(nrows=n_rows, ncols=n_cols, figsize=(5 * n_cols, 5 * n_rows))
    axes = axes.flatten()  # Flatten the array of axes if more than one row or column

    metrics = [
        ('train/reward', 'Reward'),
        ('train/actor_loss', 'Actor Loss'),
        ('train/ent_coef_loss', 'Entropy coefficient Loss'),
        ('train/ent_coef', 'Entropy coefficient'),
        ('train/critic_loss', 'Critic Loss')
    ]

    # Plot each metric
    for ax, (metric, title) in zip(axes, metrics):
        ax.plot(df['time/total_timesteps'], df[metric], label=title)
        ax.set_xlabel('Total Timesteps')
        ax.set_ylabel(title)
        ax.set_title(title)
        ax.grid(True)
        ax.legend()

    plt.tight_layout()
    plt.savefig(f'resultadosTFG/set_1+/sac/trainingStatsResults.png')
    plt.close()

df = learning_process
plot_metrics(df, n_rows=5, n_cols=1)  # Modify n_rows and n_cols as needed

# Testing

There is a new environment for testing

We feed the environment with the testing dataset we prepared before (from start test date to end test date: with closing prices, etc)

In [64]:
e_trade_gym = StockTradingEnv(df = trade, turbulence_threshold = 70,risk_indicator_col='vix', **env_kwargs)
e_trade_gym

Environment from Stable baselines3; observations is a matrix containing the inputs {balance, close price, shares, N-technical indicators}

In [65]:
env_trade, obs_trade = e_trade_gym.get_sb_env()
env_trade

In [66]:
obs_trade

array([[ 1.00000000e+06,  1.40653488e+02,  1.95822235e+02,
         1.67727432e+02,  2.26000000e+02,  1.83513992e+02,
         2.74900909e+02,  5.07116737e+01,  9.38071213e+01,
         1.75438217e+02,  3.52330658e+02,  3.07771057e+02,
         2.03622482e+02,  1.20424377e+02,  5.01258240e+01,
         1.48433228e+02,  1.54524506e+02,  4.87658424e+01,
         2.28277771e+02,  1.26340294e+02,  7.50691071e+01,
         2.82857422e+02,  1.42315781e+02,  1.30338409e+02,
         1.43675735e+02,  3.77384979e+02,  2.25689636e+02,
         4.58676758e+01,  4.03038216e+01,  4.38215218e+01,
         0.00000000e+00,  0.00000000e+00,  0.00000000e+00,
         0.00000000e+00,  0.00000000e+00,  0.00000000e+00,
         0.00000000e+00,  0.00000000e+00,  0.00000000e+00,
         0.00000000e+00,  0.00000000e+00,  0.00000000e+00,
         0.00000000e+00,  0.00000000e+00,  0.00000000e+00,
         0.00000000e+00,  0.00000000e+00,  0.00000000e+00,
         0.00000000e+00,  0.00000000e+00,  0.00000000e+0

In [67]:
trade

date   tic        open        high         low       close  \
0    2021-10-01  AAPL  141.899994  142.919998  139.110001  140.653488   
0    2021-10-01  AMGN  213.589996  214.610001  210.800003  195.822235   
0    2021-10-01   AXP  168.500000  175.119995  168.479996  167.727432   
0    2021-10-01    BA  222.850006  226.720001  220.600006  226.000000   
0    2021-10-01   CAT  192.899994  195.869995  191.240005  183.513992   
..          ...   ...         ...         ...         ...         ...   
352  2023-02-27   UNH  488.769989  490.940002  481.959991  472.278198   
352  2023-02-27     V  220.729996  221.440002  219.339996  218.230591   
352  2023-02-27    VZ   38.990002   39.150002   38.630001   35.602486   
352  2023-02-27   WBA   36.049999   36.080002   35.270000   32.621925   
352  2023-02-27   WMT   47.570000   47.696667   46.886665   46.121086   

         volume  day  high_5_sma        boll   stochrsi        adx  \
0    94639600.0  4.0  144.492001  145.480988  36.066167  51.586046   
0     2629400.0  4.0  215.557999  197.962447  75.148849  33.147887   
0     3956000.0  4.0  175.300000  159.502592  65.456038  23.039918   
0     9113600.0  4.0  227.198001  216.318501  95.477772  13.576357   
0     3695500.0  4.0  199.956000  189.037464  66.701625  33.844287   
..          ...  ...         ...         ...        ...        ...   
352   3006200.0  0.0  494.414001  476.145312  32.661437  11.867177   
352   4255300.0  0.0  221.592001  224.423517   7.819466  41.614291   
352  14210900.0  0.0   39.360000   36.881721  26.473435  40.124667   
352   5580100.0  0.0   36.282000   33.398429   2.329875  26.347004   
352  16647300.0  0.0   48.407333   46.782871  15.558425  24.757027   

     close_75_z        ao        vix  turbulence  
0     -0.448095 -5.508792  21.100000  120.031195  
0     -1.460555 -6.445471  21.100000  120.031195  
0      1.450819  8.481735  21.100000  120.031195  
0      0.034531  6.024826  21.100000  120.031195  
0     -2.043575 -7.286470  21.100000  120.031195  
..          ...       ...        ...         ...  
352   -1.131985  1.691383  20.950001    7.163887  
352    0.455638 -4.844647  20.950001    7.163887  
352   -0.081318 -1.411559  20.950001    7.163887  
352   -1.184411 -0.406441  20.950001    7.163887  
352   -0.969926 -0.022863  20.950001    7.163887  

[10237 rows x 16 columns]

## A2C

Test, predict

In [68]:
trained_model = trained_a2c
df_account_value_a2c, df_actions_a2c = DRLAgent.DRL_prediction(
    model=trained_model, 
    environment = e_trade_gym)

el modelo es 
estos son los test obs
[[ 1.00000000e+06  1.40653488e+02  1.95822235e+02  1.67727432e+02
   2.26000000e+02  1.83513992e+02  2.74900909e+02  5.07116737e+01
   9.38071213e+01  1.75438217e+02  3.52330658e+02  3.07771057e+02
   2.03622482e+02  1.20424377e+02  5.01258240e+01  1.48433228e+02
   1.54524506e+02  4.87658424e+01  2.28277771e+02  1.26340294e+02
   7.50691071e+01  2.82857422e+02  1.42315781e+02  1.30338409e+02
   1.43675735e+02  3.77384979e+02  2.25689636e+02  4.58676758e+01
   4.03038216e+01  4.38215218e+01  0.00000000e+00  0.00000000e+00
   0.00000000e+00  0.00000000e+00  0.00000000e+00  0.00000000e+00
   0.00000000e+00  0.00000000e+00  0.00000000e+00  0.00000000e+00
   0.00000000e+00  0.00000000e+00  0.00000000e+00  0.00000000e+00
   0.00000000e+00  0.00000000e+00  0.00000000e+00  0.00000000e+00
   0.00000000e+00  0.00000000e+00  0.00000000e+00  0.00000000e+00
   0.00000000e+00  0.00000000e+00  0.00000000e+00  0.00000000e+00
   0.00000000e+00  0.00000000e+00  0.00

Plot and Save testing results, Portfolio Value

In [69]:
df_account_value_a2c['date'] = pd.to_datetime(df_account_value_a2c['date']).dt.normalize()
plt.figure(figsize=(14, 7))
plt.plot(df_account_value_a2c['date'], df_account_value_a2c['account_value'])

# Setting major locator
locator = mdates.MonthLocator(interval=1)  # Show a tick every week
plt.gca().xaxis.set_major_locator(locator)

# Setting formatter
formatter = mdates.DateFormatter('%Y-%m-%d')
plt.gca().xaxis.set_major_formatter(formatter)

# Optionally, auto-format date labels to prevent overlap
plt.gcf().autofmt_xdate()

plt.title('Account Value Testing for A2C')
plt.xlabel('Date')
plt.ylabel('Account Value')
plt.grid(True)

plt.savefig(f'resultadosTFG/set_1+/a2c/testing/accountValue.png')
plt.close()

Trades made in testing

In [70]:
display(df_actions_a2c)

AAPL  AMGN  AXP  BA  CAT  CRM  CSCO  CVX  DIS   GS  ...  MRK  \
date                                                            ...        
2021-10-01    53     0  100   0   88    0   100   82    0   95  ...   42   
2021-10-04    53     0  100   0   88    0   100   82    0   95  ...   42   
2021-10-05    42     0  100   0  100    0   100   98    0  100  ...   26   
2021-10-06    42     0  100   0  100    0   100   98    0  100  ...   26   
2021-10-07     0     0  100   0  100    0   100  100    0   28  ...    0   
...          ...   ...  ...  ..  ...  ...   ...  ...  ...  ...  ...  ...   
2023-02-17     0     0    0   0    0    0     0    0    0    0  ...    0   
2023-02-21     0     0    0   0    0    0     0    0    0    0  ...    0   
2023-02-22     0     0    0   0    0    0     0    0    0    0  ...    0   
2023-02-23     0     0    0   0    0    0     0    0    0    0  ...    0   
2023-02-24     0     0    0   0    0    0     0    0    0    0  ...    0   

            MSFT  NKE  PG  TRV  UNH    V  VZ  WBA  WMT  
date                                                    
2021-10-01   100   14   0  100   33   81   0  100   39  
2021-10-04   100   14   0  100   33   81   0  100   39  
2021-10-05   100   27   0  100   33   91   0  100   39  
2021-10-06   100   27   0  100   33   91   0  100   39  
2021-10-07   100    0   0  100    0  100   0  100    0  
...          ...  ...  ..  ...  ...  ...  ..  ...  ...  
2023-02-17     0    0   0    0    0    0   0    0    0  
2023-02-21     0    0   0    0    0    0   0    0    0  
2023-02-22     0    0   0    0    0    0   0    0    0  
2023-02-23     0    0   0    0    0    0   0    0    0  
2023-02-24     0    0   0    0    0    0   0    0    0  

[352 rows x 29 columns]

## PPO

Test, predict

In [71]:
trained_model = trained_ppo
df_account_value_ppo, df_actions_ppo = DRLAgent.DRL_prediction(
    model=trained_model, 
    environment = e_trade_gym)

el modelo es 
estos son los test obs
[[ 1.00000000e+06  1.40653488e+02  1.95822235e+02  1.67727432e+02
   2.26000000e+02  1.83513992e+02  2.74900909e+02  5.07116737e+01
   9.38071213e+01  1.75438217e+02  3.52330658e+02  3.07771057e+02
   2.03622482e+02  1.20424377e+02  5.01258240e+01  1.48433228e+02
   1.54524506e+02  4.87658424e+01  2.28277771e+02  1.26340294e+02
   7.50691071e+01  2.82857422e+02  1.42315781e+02  1.30338409e+02
   1.43675735e+02  3.77384979e+02  2.25689636e+02  4.58676758e+01
   4.03038216e+01  4.38215218e+01  0.00000000e+00  0.00000000e+00
   0.00000000e+00  0.00000000e+00  0.00000000e+00  0.00000000e+00
   0.00000000e+00  0.00000000e+00  0.00000000e+00  0.00000000e+00
   0.00000000e+00  0.00000000e+00  0.00000000e+00  0.00000000e+00
   0.00000000e+00  0.00000000e+00  0.00000000e+00  0.00000000e+00
   0.00000000e+00  0.00000000e+00  0.00000000e+00  0.00000000e+00
   0.00000000e+00  0.00000000e+00  0.00000000e+00  0.00000000e+00
   0.00000000e+00  0.00000000e+00  0.00

Save Plot of Portfolio Value

In [72]:
df_account_value_ppo['date'] = pd.to_datetime(df_account_value_ppo['date']).dt.normalize()
plt.figure(figsize=(14, 7))
plt.plot(df_account_value_ppo['date'], df_account_value_ppo['account_value'])

# Setting major locator
locator = mdates.MonthLocator(interval=1)  # Show a tick every week
plt.gca().xaxis.set_major_locator(locator)

# Setting formatter
formatter = mdates.DateFormatter('%Y-%m-%d')
plt.gca().xaxis.set_major_formatter(formatter)

# Optionally, auto-format date labels to prevent overlap
plt.gcf().autofmt_xdate()

plt.title('Account Value Testing for PPO')
plt.xlabel('Date')
plt.ylabel('Account Value')
plt.grid(True)

plt.savefig(f'resultadosTFG/set_1+/ppo/testing/accountValue.png')
plt.close()


Trades made in testing

In [73]:
df_actions_ppo.tail(40)

AAPL  AMGN  AXP  BA  CAT  CRM  CSCO  CVX  DIS  GS  ...  MRK  MSFT  \
date                                                           ...              
2022-12-28     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2022-12-29     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2022-12-30     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-01-03     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-01-04     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-01-05     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-01-06     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-01-09     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-01-10     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-01-11     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-01-12     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-01-13     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-01-17     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-01-18     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-01-19     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-01-20     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-01-23     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-01-24     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-01-25     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-01-26     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-01-27     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-01-30     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-01-31     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-02-01     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-02-02     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-02-03     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-02-06     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-02-07     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-02-08     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-02-09     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-02-10     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-02-13     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-02-14     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-02-15     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-02-16     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-02-17     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-02-21     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-02-22     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-02-23     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-02-24     0     0    0   0    0    0     0    0    0   0  ...    0     0   

            NKE  PG  TRV  UNH  V  VZ  WBA  WMT  
date                                            
2022-12-28    0   0    0    0  0   0    0    8  
2022-12-29    0   0    0    0  0   0    0   11  
2022-12-30    0   0    0    0  0   0    0   14  
2023-01-03    0   0    0    0  0   1    0    5  
2023-01-04    0   0    0    0  0   0    0    0  
2023-01-05    0   0    0    0  0   0    0    5  
2023-01-06    0   0    0    0  0   0    0    0  
2023-01-09    0   0    0    0  0   0    0    0  
2023-01-10    0   0    0    0  0   0    0    0  
2023-01-11    0   0    0    0  0   1    0   16  
2023-01-12    0   0  

## DDPG

Test DDPG, predict

In [74]:
trained_model = trained_ddpg
df_account_value_ddpg, df_actions_ddpg = DRLAgent.DRL_prediction(
    model=trained_model, 
    environment = e_trade_gym)

el modelo es 
estos son los test obs
[[ 1.00000000e+06  1.40653488e+02  1.95822235e+02  1.67727432e+02
   2.26000000e+02  1.83513992e+02  2.74900909e+02  5.07116737e+01
   9.38071213e+01  1.75438217e+02  3.52330658e+02  3.07771057e+02
   2.03622482e+02  1.20424377e+02  5.01258240e+01  1.48433228e+02
   1.54524506e+02  4.87658424e+01  2.28277771e+02  1.26340294e+02
   7.50691071e+01  2.82857422e+02  1.42315781e+02  1.30338409e+02
   1.43675735e+02  3.77384979e+02  2.25689636e+02  4.58676758e+01
   4.03038216e+01  4.38215218e+01  0.00000000e+00  0.00000000e+00
   0.00000000e+00  0.00000000e+00  0.00000000e+00  0.00000000e+00
   0.00000000e+00  0.00000000e+00  0.00000000e+00  0.00000000e+00
   0.00000000e+00  0.00000000e+00  0.00000000e+00  0.00000000e+00
   0.00000000e+00  0.00000000e+00  0.00000000e+00  0.00000000e+00
   0.00000000e+00  0.00000000e+00  0.00000000e+00  0.00000000e+00
   0.00000000e+00  0.00000000e+00  0.00000000e+00  0.00000000e+00
   0.00000000e+00  0.00000000e+00  0.00

Store graph of the value of portfolio

In [75]:
df_account_value_ddpg['date'] = pd.to_datetime(df_account_value_ddpg['date']).dt.normalize()
plt.figure(figsize=(14, 7))
plt.plot(df_account_value_ddpg['date'], df_account_value_ddpg['account_value'])

# Setting major locator
locator = mdates.MonthLocator(interval=1)  # Show a tick every week
plt.gca().xaxis.set_major_locator(locator)

# Setting formatter
formatter = mdates.DateFormatter('%Y-%m-%d')
plt.gca().xaxis.set_major_formatter(formatter)

# Optionally, auto-format date labels to prevent overlap
plt.gcf().autofmt_xdate()

plt.title('Account Value Testing for DDPG')
plt.xlabel('Date')
plt.ylabel('Account Value')
plt.grid(True)

plt.savefig(f'resultadosTFG/set_1+/ddpg/testing/accountValue.png')
plt.close()


Trades made in testing

In [76]:
df_actions_ddpg.head(30)

AAPL  AMGN  AXP   BA  CAT  CRM  CSCO  CVX  DIS   GS  ...  MRK  \
date                                                             ...        
2021-10-01     0   100    0  100    0    0     0  100    0  100  ...  100   
2021-10-04     0   100    0  100    0    0     0  100    0  100  ...  100   
2021-10-05     0   100    0  100    0    0     0  100    0  100  ...  100   
2021-10-06     0     0    0  100    0    0     0  100    0    0  ...  100   
2021-10-07     0     0    0    0    0    0     0    0    0    0  ...    0   
2021-10-08     0     0    0    0    0    0     0    0    0    0  ...    0   
2021-10-11     0     0    0    0    0    0     0    0    0    0  ...    0   
2021-10-12     0     0    0    0    0    0     0    1    0    0  ...    0   
2021-10-13     0     0    0    0    0    0     0    0    0    0  ...    0   
2021-10-14     0     0    0    0    0    0     0    0    0    0  ...    0   
2021-10-15     0     0    0    0    0    0     0    0    0    0  ...    0   
2021-10-18     0     0    0    0    0    0     0    0    0    0  ...    0   
2021-10-19     0     0    0    0    0    0     0    0    0    0  ...    0   
2021-10-20     0     0    0    0    0    0     0    0    0    0  ...    0   
2021-10-21     0     0    0    0    0    0     0    0    0    0  ...    0   
2021-10-22     0     0    0    0    0    0     0    0    0    0  ...    0   
2021-10-25     0     0    0    0    0    0     0    0    0    0  ...    0   
2021-10-26     0     0    0    0    0    0     0    0    0    0  ...    0   
2021-10-27     0     0    0    0    0    0     0    0    0    0  ...    0   
2021-10-28     0     0    0    0    0    0     0    0    0    0  ...    0   
2021-10-29     0     0    0    0    0    0     0    0    0    0  ...    0   
2021-11-01     0     0    0    0    0    0     0    0    0    0  ...    0   
2021-11-02     0     0    0    0    0    0     0    0    0    0  ...    0   
2021-11-03     0     0    0    0    0    0     0    0    0    0  ...    0   
2021-11-04     0     0    0    0    0    0     0    0    0    0  ...    0   
2021-11-05     0     0    0    0    0    0     0    0    0    0  ...    0   
2021-11-08     0     0    0    0    0    0     0    0    0    0  ...    0   
2021-11-09     0     0    0    0    0    0     0    0    0    0  ...    0   
2021-11-10     0     0    0    0    0    0     0    0    0    0  ...    0   
2021-11-11     0     0    0    0    0    0     0    0    0    0  ...    0   

            MSFT  NKE  PG  TRV  UNH  V  VZ  WBA  WMT  
date                                                  
2021-10-01   100    0   0  100  100  0   0    0  100  
2021-10-04   100    0   0  100  100  0   0    0  100  
2021-10-05   100    0   0  100  100  0   0    0  100  
2021-10-06   100    0   0   37    0  0   0    0  100  
2021-10-07     0    0   0    0    0  0   0    0  100  
2021-10-08     0    0   0    0    0  0   0    0  100  
2021-10-11     0    0   0    0    0  0   0    0  100  
2021-10-12     0    0   0    0    0  0   0    0  100  
2021-10-13     0    0   0    0    0  0   0    0    0  
2021-10-14     0    0   0    0    0  0   0    0    0  
2021-10-15     0    0   0    0    0  0   0    0    0  
2021-10-18     0    0   0    0    0  0   0    0    0  
2021-10-19     0    0   0    0    0  0   0    0    0  
2021-10-20     0    0   0    0    0  0   0    0    0  
2021-10-21     0    0   0    0    0  0   0    0    0  
2021-10-22     0    0   0    0    0  0   0    0    0  
2021-10-25     0    0   0    0    0  0   0    0    0  
2021-10-26     0    0   0    0    0  0   0    0    0  
2021-10-27     0    0   0    0    0  0   0    0    0  
2021-10-28     0    0   0    0    0  0   0    0    0  
2021-10-29     0    0   0    0    0  0   0    0    0  
2021-11-01     0    0   0    0    0  0   0    0    0  
2021-11-02     0    0   0    0    0  0   0    0    0  
2021-11-03     0    0   0    0    0  0   0    0    0  
2021-11-04     0    0   0    0    0  0   0    0    0  
2021-11-05     0    0   0    0    0  0   0    0    0  
2021-11

## TD3

Test TD3, predict

In [77]:
trained_model = trained_td3
df_account_value_td3, df_actions_td3 = DRLAgent.DRL_prediction(
    model=trained_model, 
    environment = e_trade_gym)

el modelo es 
estos son los test obs
[[ 1.00000000e+06  1.40653488e+02  1.95822235e+02  1.67727432e+02
   2.26000000e+02  1.83513992e+02  2.74900909e+02  5.07116737e+01
   9.38071213e+01  1.75438217e+02  3.52330658e+02  3.07771057e+02
   2.03622482e+02  1.20424377e+02  5.01258240e+01  1.48433228e+02
   1.54524506e+02  4.87658424e+01  2.28277771e+02  1.26340294e+02
   7.50691071e+01  2.82857422e+02  1.42315781e+02  1.30338409e+02
   1.43675735e+02  3.77384979e+02  2.25689636e+02  4.58676758e+01
   4.03038216e+01  4.38215218e+01  0.00000000e+00  0.00000000e+00
   0.00000000e+00  0.00000000e+00  0.00000000e+00  0.00000000e+00
   0.00000000e+00  0.00000000e+00  0.00000000e+00  0.00000000e+00
   0.00000000e+00  0.00000000e+00  0.00000000e+00  0.00000000e+00
   0.00000000e+00  0.00000000e+00  0.00000000e+00  0.00000000e+00
   0.00000000e+00  0.00000000e+00  0.00000000e+00  0.00000000e+00
   0.00000000e+00  0.00000000e+00  0.00000000e+00  0.00000000e+00
   0.00000000e+00  0.00000000e+00  0.00

Store graph of the value of portfolio

In [78]:
df_account_value_td3['date'] = pd.to_datetime(df_account_value_td3['date']).dt.normalize()
plt.figure(figsize=(14, 7))
plt.plot(df_account_value_td3['date'], df_account_value_td3['account_value'])

# Setting major locator
locator = mdates.MonthLocator(interval=1)  # Show a tick every week
plt.gca().xaxis.set_major_locator(locator)

# Setting formatter
formatter = mdates.DateFormatter('%Y-%m-%d')
plt.gca().xaxis.set_major_formatter(formatter)

# Optionally, auto-format date labels to prevent overlap
plt.gcf().autofmt_xdate()

plt.title('Account Value Testing for TD3')
plt.xlabel('Date')
plt.ylabel('Account Value')
plt.grid(True)

plt.savefig(f'resultadosTFG/set_1+/td3/testing/accountValue.png')
plt.close()


Trades made in testing

In [79]:
df_actions_td3.head(30)

AAPL  AMGN  AXP   BA  CAT  CRM  CSCO  CVX  DIS  GS  ...  MRK  \
date                                                            ...        
2021-10-01     0     0  100  100  100  100   100    0    0   0  ...    0   
2021-10-04     0     0  100  100  100  100   100    0    0   0  ...    0   
2021-10-05     0     0  100  100  100  100   100    0    0   0  ...    0   
2021-10-06     0     0    1  100  100  100   100    0    0   0  ...    0   
2021-10-07     0     0    0   91    0    0     0    0    0   0  ...    0   
2021-10-08     0     0    0   90    0    0     0    0    0   0  ...    0   
2021-10-11     0     0    0   89    0    0     0    0    0   0  ...    0   
2021-10-12     0     0    0   90    0    0     0    0    0   0  ...    0   
2021-10-13     0     0    0    0    0    0     0    0    0   0  ...    0   
2021-10-14     0     0    0    0    0    0     0    0    0   0  ...    0   
2021-10-15     0     0    0    0    0    0     0    0    0   0  ...    0   
2021-10-18     0     0    0    0    0    0     0    0    0   0  ...    0   
2021-10-19     0     0    0    0    0    0     0    0    0   0  ...    0   
2021-10-20     0     0    0    0    0    0     0    0    0   0  ...    0   
2021-10-21     0     0    0    0    0    0     0    0    0   0  ...    0   
2021-10-22     0     0    0    0    0    0     0    0    0   0  ...    0   
2021-10-25     0     0    0    0    0    0     0    0    0   0  ...    0   
2021-10-26     0     0    0    0    0    0     0    0    0   0  ...    0   
2021-10-27     0     0    0    0    0    0     0    0    0   0  ...    0   
2021-10-28     0     0    0    0    0    0     0    0    0   0  ...    0   
2021-10-29     0     0    0    0    0    0     0    0    0   0  ...    0   
2021-11-01     0     0    0    0    0    0     0    0    0   0  ...    0   
2021-11-02     0     0    0    0    0    0     0    0    0   0  ...    0   
2021-11-03     0     0    0    0    0    0     0    0    0   0  ...    0   
2021-11-04     0     0    0    0    0    0     0    0    0   0  ...    0   
2021-11-05     0     0    0    0    0    0     0    0    0   0  ...    0   
2021-11-08     0     0    0    0    0    0     0    0    0   0  ...    0   
2021-11-09     0     0    0    0    0    0     0    0    0   0  ...    0   
2021-11-10     0     0    0    0    0    0     0    0    0   0  ...    0   
2021-11-11     0     0    0    0    0    0     0    0    0   0  ...    0   

            MSFT  NKE   PG  TRV  UNH  V  VZ  WBA  WMT  
date                                                   
2021-10-01   100    0  100  100  100  0   0  100    0  
2021-10-04   100    0  100  100  100  0   0  100    0  
2021-10-05   100    0  100  100  100  0   0  100    0  
2021-10-06   100    0  100  100   86  0   0  100    0  
2021-10-07     0    0    0    0    0  0   0    1    0  
2021-10-08     0    0    0    0    0  0   0    1    0  
2021-10-11     0    0    0    0    0  0   0    0    0  
2021-10-12     0    0    0    0    0  0   0    2    0  
2021-10-13     0    0    0    0    0  0   0    0    0  
2021-10-14     0    0    0    0    0  0   0    0    0  
2021-10-15     0    0    0    0    0  0   0    0    0  
2021-10-18     0    0    0    0    0  0   0    0    0  
2021-10-19     0    0    0    0    0  0   0    0    0  
2021-10-20     0    0    0    0    0  0   0    0    0  
2021-10-21     0    0    0    0    0  0   0    0    0  
2021-10-22     0    0    0    0    0  0   0    0    0  
2021-10-25     0    0    0    0    0  0   0    0    0  
2021-10-26     0    0    0    0    0  0   0    0    0  
2021-10-27     0    0    0    0    0  0   0    0    0  
2021-10-28     0    0    0    0    0  0   0    0    0  
2021-10-29     0    0    0    0    0  0   0    0    0  
2021-11-01     0    0    0    0    0  0   0    0    0  
2021-11-02     0    0    0    0    0  0   0    0    0  
2021-11-03     0    0    0    0    0  0   0    0    0  
2021-11-04     0    0    0    0    0  0   0    0    0  
2021-11-05     0    0    0    0    0  0   0    0    0  
2021-11-08 

## SAC

Test SAC, predict

Account value is the DF that stores the history of the value of the assets (portfolio value)

In [80]:
trained_model = trained_sac
df_account_value_sac, df_actions_sac = DRLAgent.DRL_prediction(
    model=trained_model, 
    environment = e_trade_gym)

el modelo es 
estos son los test obs
[[ 1.00000000e+06  1.40653488e+02  1.95822235e+02  1.67727432e+02
   2.26000000e+02  1.83513992e+02  2.74900909e+02  5.07116737e+01
   9.38071213e+01  1.75438217e+02  3.52330658e+02  3.07771057e+02
   2.03622482e+02  1.20424377e+02  5.01258240e+01  1.48433228e+02
   1.54524506e+02  4.87658424e+01  2.28277771e+02  1.26340294e+02
   7.50691071e+01  2.82857422e+02  1.42315781e+02  1.30338409e+02
   1.43675735e+02  3.77384979e+02  2.25689636e+02  4.58676758e+01
   4.03038216e+01  4.38215218e+01  0.00000000e+00  0.00000000e+00
   0.00000000e+00  0.00000000e+00  0.00000000e+00  0.00000000e+00
   0.00000000e+00  0.00000000e+00  0.00000000e+00  0.00000000e+00
   0.00000000e+00  0.00000000e+00  0.00000000e+00  0.00000000e+00
   0.00000000e+00  0.00000000e+00  0.00000000e+00  0.00000000e+00
   0.00000000e+00  0.00000000e+00  0.00000000e+00  0.00000000e+00
   0.00000000e+00  0.00000000e+00  0.00000000e+00  0.00000000e+00
   0.00000000e+00  0.00000000e+00  0.00

Store graph of the value of portfolio

In [81]:
df_account_value_sac['date'] = pd.to_datetime(df_account_value_sac['date']).dt.normalize()
plt.figure(figsize=(14, 7))
plt.plot(df_account_value_sac['date'], df_account_value_sac['account_value'])

# Setting major locator
locator = mdates.MonthLocator(interval=1)  # Show a tick every week
plt.gca().xaxis.set_major_locator(locator)

# Setting formatter
formatter = mdates.DateFormatter('%Y-%m-%d')
plt.gca().xaxis.set_major_formatter(formatter)

# Optionally, auto-format date labels to prevent overlap
plt.gcf().autofmt_xdate()

plt.title('Account Value Testing for SAC')
plt.xlabel('Date')
plt.ylabel('Account Value')
plt.grid(True)

plt.savefig(f'resultadosTFG/set_1+/sac/testing/accountValue.png')
plt.close()


Trades made in testing

In [82]:
df_actions_sac.head(30)

AAPL  AMGN  AXP  BA  CAT  CRM  CSCO  CVX  DIS  GS  ...  MRK  MSFT  \
date                                                           ...              
2021-10-01    38    92    0  97   75   96     0    0    0   0  ...    0     0   
2021-10-04    38    92    0  97   75   96     0    0    0   0  ...    0     0   
2021-10-05    38    92    0  97   75   96     0    0    0   0  ...    0     0   
2021-10-06    38    92    0  97   75   96     0    0    0   0  ...    0     0   
2021-10-07    38    92    0  97   75   96     0    0    0   0  ...    0     0   
2021-10-08     0     0    0  97    0   96     0    0    0   0  ...    0     0   
2021-10-11   -95   -90    0  99    0    0     0    0    0   0  ...    0     0   
2021-10-12   -75   -78    0  99    0    0     0    0    0   0  ...    0     0   
2021-10-13   -20   -59    0  77    0    0     0    0    0   0  ...    0     0   
2021-10-14     0   -67    0  61    0    0     0    0    0   0  ...    0     0   
2021-10-15     0   -47    0  16  -27    0     0    0    0   0  ...    0     0   
2021-10-18     0   -10    0   0  -41    0     0    0    0   0  ...    0     0   
2021-10-19     0     0    0   0  -44    0     0    0    0   0  ...    0     0   
2021-10-20     0     0    0   0  -46    0     0    0    0   0  ...    0     0   
2021-10-21     0     0    0   0  -51    0     0    0    0   0  ...    0     0   
2021-10-22     0     0    0   7  -60    0     0    0    0   0  ...    0     0   
2021-10-25     0     0    0   0  -63    0     0    0    0   0  ...    0     0   
2021-10-26     0     0    0   0  -43    0     0    0    0   0  ...    0     0   
2021-10-27     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2021-10-28     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2021-10-29     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2021-11-01     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2021-11-02     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2021-11-03     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2021-11-04     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2021-11-05     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2021-11-08     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2021-11-09     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2021-11-10     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2021-11-11     0     0    0   0    0    0     0    0    0   0  ...    0     0   

            NKE  PG  TRV  UNH   V  VZ  WBA  WMT  
date                                             
2021-10-01    0  95   94    0  94  85   87   94  
2021-10-04    0  95   94    0  94  85   87   94  
2021-10-05    0  95   94    0  94  85   87   94  
2021-10-06    0  95   94    0  94  85   87   94  
2021-10-07    0  95   94    0  94  85   87   94  
2021-10-08    0  95   38    0  94   0    1   94  
2021-10-11    0  68    0    0 -94 -97  -96    0  
2021-10-12    0  99    0    0 -87 -96  -90  -43  
2021-10-13    0   0    0    0 -75 -95  -85  -85  
2021-10-14    0   0    0    0 -57 -96  -76  -97  
2021-10-15    0   0    0    0 -24 -41  -45  -99  
2021-10-18    0   0    0    0   0   0    0  -99  
2021-10-19    0   0    0    0   0   0  -18  -99  
2021-10-20    0   0    0    0   0   0  -26  -42  
2021-10-21    0   0    0    0   0   0    0    0  
2021-10-22    0  99    0    0   0   0    0    0  
2021-10-25    0   0    0    0   0   0    0    0  
2021-10-26    0   0    0    0   0   0    0    0  
2021-10-27    0   0    0    0   0   0    0    0  
2021-10-28    0   0    0    0   0   0    0    0  
2021-10-29    0   0    0    0   0   0    0    0  
2021-11-01    0   0    0    0   0   0    0    0  
2021-11-02    0   0    0    0   0   0    0    0  
2021-11-03    0   0    0    0   0   0    0    0  
2021-11-04    0   0    0    0   0   0    0    0  
2021-11-05    0   0    0    0   0   0    0    0  
2021-11-08    0   0

Obtain results to then merge: merge in one DF the Portfolio Value given by each algorithm

In [83]:
df_result_a2c = df_account_value_a2c.set_index(df_account_value_a2c.columns[0])
df_result_a2c.rename(columns = {'account_value':'a2c'}, inplace = True)
df_result_ddpg = df_account_value_ddpg.set_index(df_account_value_ddpg.columns[0])
df_result_ddpg.rename(columns = {'account_value':'ddpg'}, inplace = True)
df_result_td3 = df_account_value_td3.set_index(df_account_value_td3.columns[0])
df_result_td3.rename(columns = {'account_value':'td3'}, inplace = True)
df_result_ppo = df_account_value_ppo.set_index(df_account_value_ppo.columns[0])
df_result_ppo.rename(columns = {'account_value':'ppo'}, inplace = True)
df_result_sac = df_account_value_sac.set_index(df_account_value_sac.columns[0])
df_result_sac.rename(columns = {'account_value':'sac'}, inplace = True)

We can also get stats from each stock individually (even though the analysis won't focus on that)

In [84]:
#baseline stats

print("==============Get Baseline Stats===========")
print("==============Baseline Stats of Profitability from DJIA===========")
print("This is the real performance of the index")
df_dji_ = get_baseline(
        ticker="^DJI", 
        start = TEST_START_DATE,
        end = TEST_END_DATE)
stats = backtest_stats(df_dji_, value_col_name = 'close')

==============Get Baseline Stats===========
==============Baseline Stats of Profitability from DJIA===========
This is the real performance of the index


[*********************100%%**********************]  1 of 1 completed

Shape of DataFrame:  (354, 8)
Annual return         -0.034876
Cumulative returns    -0.048644
Annual volatility      0.181612
Sharpe ratio          -0.105351
Calmar ratio          -0.158953
Stability              0.280983
Max drawdown          -0.219408
Omega ratio            0.982546
Sortino ratio         -0.146974
Skew                        NaN
Kurtosis                    NaN
Tail ratio             0.970602
Daily value at risk   -0.022957
dtype: float64


get_baseline vuelve a fetchear los stocks de YahooFinance dadas esas fechas.

backtest_stats llama a get daily return y luego saca stats de esa Serie con metodo que pide:

    """
    Calculates various performance metrics of a strategy, for use in
    plotting.show_perf_stats.

    Parameters
    ----------
    returns : pd.Series
        Daily returns of the strategy, noncumulative.
         - See full explanation in tears.create_full_tear_sheet.
    factor_returns : pd.Series, optional
        Daily noncumulative returns of the benchmark factor to which betas are
        computed. Usually a benchmark such as market returns.
         - This is in the same style as returns.
         - If None, do not compute alpha, beta, and information ratio.
    positions : pd.DataFrame
        Daily net position values.
         - See full explanation in tears.create_full_tear_sheet.
    transactions : pd.DataFrame
        Prices and amounts of executed trades. One row per trade.
        - See full explanation in tears.create_full_tear_sheet.
    turnover_denom : str
        Either AGB or portfolio_value, default AGB.
        - See full explanation in txn.get_turnover.

    Returns
    -------
    pd.Series
        Performance metrics.
    """

get daily profitability * invested amount = portfolio value in case of investing 1000000$ on DJ and not touching it

In [85]:
df_dji = pd.DataFrame()
df_dji['date'] = df_account_value_a2c['date']
df_dji['account_value'] = df_dji_['close'] / df_dji_['close'][0] * env_kwargs["initial_amount"] # get daily profitability * invested amount = portfolio value in case of investing 1000000$ on DJ and not touching it
#df_dji.to_csv("df_dji.csv")
df_dji = df_dji.set_index(df_dji.columns[0])
#df_dji.to_csv("df_dji+.csv")

In [86]:
df_dji.rename(columns = {'account_value':'dji'}, inplace = True)

In [87]:
df_result_td3

td3
date                    
2021-10-01  1.000000e+06
2021-10-04  9.971198e+05
2021-10-05  1.001176e+06
2021-10-06  1.004311e+06
2021-10-07  1.015872e+06
...                  ...
2023-02-21  9.966966e+05
2023-02-22  9.959445e+05
2023-02-23  1.001266e+06
2023-02-24  9.849864e+05
2023-02-27  9.879260e+05

[353 rows x 1 columns]

Compare DJIA with the rest of the algorithms

In [88]:
result = pd.DataFrame()
result = pd.merge(result, df_result_a2c, how='outer', left_index=True, right_index=True)
result = pd.merge(result, df_result_ddpg, how='outer', left_index=True, right_index=True)
result = pd.merge(result, df_result_td3, how='outer', left_index=True, right_index=True)
result = pd.merge(result, df_result_ppo, how='outer', left_index=True, right_index=True)
result = pd.merge(result, df_result_sac, how='outer', left_index=True, right_index=True)
result = pd.merge(result, df_dji, how='outer', left_index=True, right_index=True)
display(result)

a2c          ddpg           td3           ppo  \
date                                                                 
2021-10-01  1.000000e+06  1.000000e+06  1.000000e+06  1.000000e+06   
2021-10-04  9.975252e+05  9.971939e+05  9.971198e+05  9.996953e+05   
2021-10-05  1.002537e+06  1.003573e+06  1.001176e+06  1.000034e+06   
2021-10-06  1.004259e+06  1.005684e+06  1.004311e+06  1.000035e+06   
2021-10-07  1.013232e+06  1.015256e+06  1.015872e+06  1.001313e+06   
...                  ...           ...           ...           ...   
2023-02-21  1.025703e+06  1.014156e+06  9.966966e+05  1.011528e+06   
2023-02-22  1.022697e+06  1.010802e+06  9.959445e+05  1.005148e+06   
2023-02-23  1.028556e+06  1.016769e+06  1.001266e+06  1.007367e+06   
2023-02-24  1.016677e+06  1.004242e+06  9.849864e+05  9.934823e+05   
2023-02-27  1.021566e+06  1.005693e+06  9.879260e+05  9.980066e+05   

                     sac           dji  
date                                    
2021-10-01  1.000000e+06  1.000000e+06  
2021-10-04  9.979509e+05  9.905746e+05  
2021-10-05  9.990689e+05  9.996566e+05  
2021-10-06  1.001376e+06  1.002637e+06  
2021-10-07  1.005681e+06  1.012483e+06  
...                  ...           ...  
2023-02-21  8.819762e+05  9.651327e+05  
2023-02-22  8.822850e+05  9.626710e+05  
2023-02-23  8.852778e+05  9.658412e+05  
2023-02-24  8.692241e+05  9.560240e+05  
2023-02-27  8.728906e+05  9.581264e+05  

[353 rows x 6 columns]

Save and Plot!

In [89]:
plt.rcParams["figure.figsize"] = (15,5)
plt.figure();
result.plot();
plt.savefig(f'resultadosTFG/set_1+/AlgorithmsVsDJI.png')
plt.close()